In [30]:
from bs4 import BeautifulSoup as bs4
import requests
import pandas as pd
import re
import time
from selenium import webdriver
from selenium.webdriver.common.keys import Keys

from webdriver_manager.chrome import ChromeDriverManager

pages=[
    "http://www.magazinelusa.com",
    "http://www.magazinelusa.com/category/wtf/",
    "http://www.magazinelusa.com/category/noticias/",
    "http://www.magazinelusa.com/category/saude/",
    "http://www.magazinelusa.com/category/famosos/",
    "http://www.magazinelusa.com/category/lifehacks/",
    "http://www.magazinelusa.com/category/criancas/",
    "http://www.magazinelusa.com/category/alertas/",
    "http://www.magazinelusa.com/category/animais/",
    "http://www.magazinelusa.com/category/desportos/",
    "http://www.magazinelusa.com/category/motivacional/"
]

urls= set()

In [31]:
driver = webdriver.Chrome(ChromeDriverManager().install())

In [32]:
for url in pages:
    # Open webpage
    driver.get(url)

    # Extract first 10 article URLs
    soup = bs4(driver.page_source, 'html.parser')
    link_elements = soup.find_all("li", class_="g1-collection-item g1-collection-item-1of3")

    for element in link_elements:
        soup = bs4(str(element), 'html.parser')
        link = soup.find('a', class_='g1-frame')
        url = link['href']
        urls.add(url)

    # Press button to load more news articles
    driver.find_element_by_class_name("g1-collection-more-inner").click()

    # Scroll down until the end of the webpage to load all news articles

    lenOfPage = driver.execute_script("window.scrollTo(0, document.body.scrollHeight);var lenOfPage=document.body.scrollHeight;return lenOfPage;")
    match=False
    while(match==False):
            lastCount = lenOfPage
            time.sleep(3)
            lenOfPage = driver.execute_script("window.scrollTo(0, document.body.scrollHeight);var lenOfPage=document.body.scrollHeight;return lenOfPage;")
            if lastCount==lenOfPage:
                match=True

    # Extract the remaining urls
    soup = bs4(driver.page_source, 'html.parser')
    link_elements = soup.find_all("li", class_="g1-collection-item g1-collection-item-1of3 g1-collection-item-added")

    for element in link_elements:
        soup = bs4(str(element), 'html.parser')
        link = soup.find('a', class_='g1-frame')
        url = link['href']
        if url not in urls:
            urls.add(url)

In [33]:
for url in urls:
    print(url)

http://www.magazinelusa.com/eis-os-25-alimentos-mais-alcalinos-previnem-o-cancro-diabetes-alzheimer-e-doencas-do-coracao/
http://www.magazinelusa.com/portugal-esta-em-5-o-lugar-dos-paises-mais-corruptos-do-mundo/
http://www.magazinelusa.com/pediatra-ve-algo-estranho-na-barriga-da-menina-mas-quando-examina-a-gemea-fica-sem-palavras/
http://www.magazinelusa.com/coloca-isto-no-teu-umbigo-e-livra-te-rapidamente-da-tosse-e-da-gripe-e-colicas-menstruais/
http://www.magazinelusa.com/jurados-ficam-cepticos-perante-uma-menina-nervosa-quando-ela-comeca-um-deles-carregar-no-botao-dourado/
http://www.magazinelusa.com/bronca-jorge-jesus-critica-lideranca-de-bruno-de-carvalho-e-pode-estar-de-saida/
http://www.magazinelusa.com/esta-conversa-terminou-de-forma-inesperada/
http://www.magazinelusa.com/rita-pereira-sai-de-portugal-em-busca-de-novas-aventuras/
http://www.magazinelusa.com/daniela-ruah-esta-de-luto-e-chora-morte/
http://www.magazinelusa.com/prisioneira-do-fogo-a-historia-desta-adolescente-de

In [34]:
# list was 4044
len(urls)

3944

In [35]:
#3944
len(set(urls))

3944

In [44]:
urls_test = [
    #"http://www.magazinelusa.com/a-madeira-tambem-ja-fez-um-video-para-donald-trump-e-esta-brutal/",
    "http://www.magazinelusa.com/toda-a-gente-esta-a-errar-no-calculo-desta-operacao/"
]

In [45]:
no_more_pages = False
proxima_check = False
titles=[]
texts=[]
sources=[]
final_urls = []

# Initialize an empty dataframe
df = pd.DataFrame(columns=['Title', 'Text', 'Source', 'URL'])

for url in urls:
    print(url)
    
    i = 2
    last_text = ''

    page = requests.get(url)
    soup = bs4(page.text, 'html.parser')

    categories = soup.find("span", class_="entry-categories-inner").get_text()
    time.sleep(1)

    if (('Anedotas' in categories) or ('Comics' in categories)):
        pass # Not useful for fake news detection
    else:
        while(not(no_more_pages)):

            page = requests.get(url)
            soup = bs4(page.text, 'html.parser')

            print(url)

            news_title_1 = soup.find("h1", class_="g1-mega g1-mega-1st entry-title").get_text()
            news_content = soup.find("div", class_="entry-content g1-typography-xl").get_text()

            # Split the text using the desired sentence as the separator
            news_text = news_content.split('Diz-nos se gostaste! A tua opinião ajuda-nos a melhorar!')[0]

            # Split the text into paragraphs
            paragraphs = news_text.split('\n')

            # Remove empty paragraphs
            paragraphs = [paragraph for paragraph in paragraphs if paragraph.strip()]

            # Remove tabs and new lines from the first line
            paragraphs[0] = paragraphs[0].replace('\t', '').replace('\n', '')

            # Remove the two spaces at the beginning of paragraphs[0]
            paragraphs[0] = paragraphs[0].lstrip()

            # Join the paragraphs into a single string
            reduced_text = '\n'.join(paragraphs)

            # Check if a subtitle exists and join both title and subtitle if so:
            try:
                news_title_2 = soup.find("h2", class_="entry-subtitle g1-gamma g1-gamma-3rd").get_text()
                news_title = news_title_1 + ' ' + news_title_2
            except:
                news_title = news_title_1

            # Try finding source
            if 'Fontes' in reduced_text.split('\n')[-1]:
                try:
                    news_source = reduced_text.split('\n')[-1].split('Fontes: ')[1]  # Extract Source
                    lines = reduced_text.splitlines()                               # Split the string into lines
                    updated_lines = lines[:-1]                                      # Exclude the last line
                    reduced_text = '\n'.join(updated_lines)                         # Join the lines back into a string
                except:
                    news_source = "n/a"
            elif 'Fonte' in reduced_text.split('\n')[-1]:
                try:
                    news_source = reduced_text.split('\n')[-1].split('Fonte: ')[1]  # Extract Source
                    lines = reduced_text.splitlines()                               # Split the string into lines
                    updated_lines = lines[:-1]                                      # Exclude the last line
                    reduced_text = '\n'.join(updated_lines)                         # Join the lines back into a string
                except:
                    news_source = "n/a" 
            else:
                news_source = "n/a" 

            # Check if there is another page of the article
            if 'Próxima' in reduced_text.split('\n')[-1]:
                proxima_check = True
                if i == 2:
                    url = url+str(i)
                else:
                    url = url.rsplit("/", 1)[0]
                    url = url+'/'+str(i)
                i+=1

                # Split the text into lines
                lines = reduced_text.split('\n')

                # Find the index of the line containing "Pages:"
                pages_index = lines.index('Pages:')

                # Select the lines before "Pages:"
                clean_lines = lines[:pages_index]

                # Join the clean lines into a string
                reduced_text = '\n'.join(clean_lines)
            else:
                no_more_pages = True

                # Remove Anterior and pages lines from text
                if proxima_check:

                    # Split the text into lines
                    lines = reduced_text.split('\n')

                    # Find the index of the line containing "Pages:"
                    pages_index = lines.index('Pages:')

                    # Select the lines before "Pages:"
                    clean_lines = lines[:pages_index]

                    # Join the clean lines into a string
                    reduced_text = '\n'.join(clean_lines)

            last_text += reduced_text
            time.sleep(3)

        # Print the reduced text
        print(news_title)
        print(last_text)
        print(news_source)
                
        titles.append(news_title)
        texts.append(last_text)
        sources.append(news_source)
        final_urls.append(url)
        no_more_pages = False
        proxima_check = False

# Create a new dataframe from the lists
new_data = pd.DataFrame({'Title': titles, 'Text': texts, 'Source': sources, 'URL': final_urls})

# Concatenate the new dataframe with the existing dataframe
df = pd.concat([df, new_data], ignore_index=True)

http://www.magazinelusa.com/eis-os-25-alimentos-mais-alcalinos-previnem-o-cancro-diabetes-alzheimer-e-doencas-do-coracao/
http://www.magazinelusa.com/eis-os-25-alimentos-mais-alcalinos-previnem-o-cancro-diabetes-alzheimer-e-doencas-do-coracao/
Eis os 25 alimentos mais alcalinos! Previnem o Cancro, Diabetes, Alzheimer e doenças do Coração! Proteja-se, consumindo-os!
Todos nós sabemos, ou deveríamos saber, que os produtos processados, açucarados e com ingredientes químicos são péssimos para a saúde, certo? Pois é, a maioria das pessoas está ciente disso, mas os "fast-foods", por exemplo, não deixam de estar cheios a qualquer hora do dia.
Esse tipo de alimento altera o pH do nosso corpo, causando consequências terríveis. O correto é que o nosso organismo seja alcalino, mas o ser humano insiste na má alimentação, acidificando o sangue.
Se não sabe, o pH ácido afecta o sistema imunológico, abrindo caminho para muitas doenças graves. Por isso, é muito importante que faça de tudo para que o s

In [53]:
len(final_urls)

3753

In [54]:
len(titles)

3753

In [55]:
len(texts)

3753

In [56]:
df.head()

Title  \
0  Eis os 25 alimentos mais alcalinos! Previnem o...   
1  Portugal está em 5.º lugar dos países Mais Cor...   
2  Pediatra vê algo estranho na Barriga da Menina...   
3  Coloca isto no teu umbigo e livra-te rapidamen...   
4  Jurados ficam cépticos perante uma menina nerv...   

                                                Text Source  \
0  Todos nós sabemos, ou deveríamos saber, que os...    n/a   
1  Portugal está em 5.º lugar dos países mais cor...    n/a   
2  Esta é a história de Alissa e Michael Dunn, um...    n/a   
3  Cada vez mais se está a perder a cultura antig...    n/a   
4  Jurados ficam cépticos perante uma menina nerv...    n/a   

                                                 URL  
0  http://www.magazinelusa.com/eis-os-25-alimento...  
1  http://www.magazinelusa.com/portugal-esta-em-5...  
2  http://www.magazinelusa.com/pediatra-ve-algo-e...  
3  http://www.magazinelusa.com/coloca-isto-no-teu...  
4  http://www.magazinelusa.com/jurados-ficam-cept...

In [57]:
df.head()
df.to_csv("Magazine_lusa_dataset.csv", index=False)

In [58]:
loaded_df = pd.read_csv("Magazine_lusa_dataset.csv")
loaded_df.head()

Title  \
0  Eis os 25 alimentos mais alcalinos! Previnem o...   
1  Portugal está em 5.º lugar dos países Mais Cor...   
2  Pediatra vê algo estranho na Barriga da Menina...   
3  Coloca isto no teu umbigo e livra-te rapidamen...   
4  Jurados ficam cépticos perante uma menina nerv...   

                                                Text Source  \
0  Todos nós sabemos, ou deveríamos saber, que os...    NaN   
1  Portugal está em 5.º lugar dos países mais cor...    NaN   
2  Esta é a história de Alissa e Michael Dunn, um...    NaN   
3  Cada vez mais se está a perder a cultura antig...    NaN   
4  Jurados ficam cépticos perante uma menina nerv...    NaN   

                                                 URL  
0  http://www.magazinelusa.com/eis-os-25-alimento...  
1  http://www.magazinelusa.com/portugal-esta-em-5...  
2  http://www.magazinelusa.com/pediatra-ve-algo-e...  
3  http://www.magazinelusa.com/coloca-isto-no-teu...  
4  http://www.magazinelusa.com/jurados-ficam-cept...

In [59]:
for source in set(df['Source']):
    print(source)

riratesair.pt
e-konomista.pt
Texto de Jéssica Pellegrini
vogue.ua/article/fashion/persona/pochemu-princessa-diana-nosila-klatch-blizko-k-grudi.html
jn.pt | Foto de Capa: publico.pt
lifestyle.sapo.pt
livredireto
zap.aeiou.pt
The Siberian Times | Cosmos Magazine
Observador
Business Insider
Hiper FM
forcaportugal.com.pt
doidices.net | Noticiario Periferico
apodrecetuga.blogspot.com
awebic.com
ConfrariaGastronómicaDoLeitãoDaBairrada
vamoslaportugal.net
Incroyable
curapelanatureza.blog.br
historiascomvalor.com
gazetapolitica.com
Facebook Jennie Runevitch / Facebook David Conn
Facebook do Dr. Álvaro Caneira (Advogado)
Adaptação | Facebook
Correio da Manhã
Facebook André Pereira (@pereiratec)
sabado.pt
asdicasdaba.blogs.sapo.pt/desafio-das-52-semanas-como-poupar-mais-210093
Texto de Danielle Daian
cmjornal.pt | pplware.sapo.pt | ptjornal.com
Renata Demôro – GNT, e Jornal O Dia – Ciencia e Saude
portalcontraordenacoes.pt
comunidadeculturaearte.com
mejoratuanimo.com
Revista Flash
lusopt.com
Tes